In [1]:
import pandas as pd
import plotly.express as px
import os
import re
from glob import glob


In [2]:
# Define the directory containing the files
directory = '/g/korbel/WORKFLOW_RESULTS'

# Pattern to match the files
pattern = re.compile(r'\/g\/korbel\/WORKFLOW_RESULTS\/202[0-3]-\d{2}-\d{2}-.*\/(.*)\/counts\/\1.info_raw')

# Initialize an empty DataFrame to store aggregated data
df_aggregated = pd.DataFrame()

# Iterate over the files in the main directory

unwanted = ["._.DS_Store", ".DS_Store", "config"]


total_list_runs = sorted(
    [e for e in os.listdir(directory) if e not in unwanted]
)

l_df = list()

for plate in total_list_runs:
    if plate.split("-")[0][:2] == "20":
        for sample in os.listdir(os.path.join(directory, plate)):
            if "sample" not in unwanted:
                counts_stats_file_path = os.path.join(directory, plate, sample, "counts", f"{sample}.info_raw")
                labels_file_path = os.path.join(directory, plate, sample, "cell_selection", "labels.tsv")

                if os.path.isfile(counts_stats_file_path):
                    if os.path.isfile(labels_file_path):

                        # print(counts_stats_file_path)
                        tmp_df_stats = pd.read_csv(counts_stats_file_path, sep="\t", skiprows=13)
                        tmp_df_stats["depictio_run_id"] = plate
                        tmp_df_labels = pd.read_csv(labels_file_path, sep="\t")
                        tmp_df_labels["depictio_run_id"] = plate
                        tmp_df_labels["cell"] = tmp_df_labels["cell"].str.replace(".sort.mdup.bam", "")
                        tmp_df = tmp_df_stats.merge(tmp_df_labels, on=["depictio_run_id", "sample", "cell"])
                        l_df.append(tmp_df)



l_df = pd.concat(l_df)
l_df["year"] = l_df["depictio_run_id"].apply(lambda r: r.split("-")[0])
l_df.to_parquet("strandscape_vizu_dev.parquet")
# TODO: push df to parquet & reuse the same for ashleys stats

l_df

sample                      cell  medbin   mapped  suppl  \
0          HG03486x02         HG03486x02PE20501      14   812416    504   
1          HG03486x02         HG03486x02PE20502      12   715809    477   
2          HG03486x02         HG03486x02PE20503      20  1220951    703   
3          HG03486x02         HG03486x02PE20504      20  1408977    790   
4          HG03486x02         HG03486x02PE20505      12   789080    505   
..                ...                       ...     ...      ...    ...   
91  FrankRevTXHiAML47  FrankRevTXHiAML47PE20592      28  1985023   1235   
92  FrankRevTXHiAML47  FrankRevTXHiAML47PE20593      24  1712951   1092   
93  FrankRevTXHiAML47  FrankRevTXHiAML47PE20594      13   957165    427   
94  FrankRevTXHiAML47  FrankRevTXHiAML47PE20595      26  1717140   1114   
95  FrankRevTXHiAML47  FrankRevTXHiAML47PE20596      33  1152795    980   

      dupl    mapq   read2    good  pass1      nb_p      nb_r  nb_a  \
0   334936   51265  212503  213208      1  0.028926  0.439206   0.1   
1   275787   50360  194299  194886      1  0.028926  0.400842   0.1   
2   521408   83466  307268  308106      1  0.028926  0.634170   0.1   
3   671594   81942  326656  327995      1  0.028926  0.675949   0.1   
4   347438   52432  194048  194657      1  0.028926  0.400715   0.1   
..     ...     ...     ...     ...    ...       ...       ...   ...   
91  978411  135468  433610  436299      1  0.150206  5.358710   0.1   
92  833322  120469  378089  379979      1  0.150206  4.659320   0.1   
93  467621   62913  211805  214399      1  0.150206  2.648270   0.1   
94  793448  122826  399109  400643      1  0.150206  4.911140   0.1   
95   19248   99886  515029  517652      1  0.150206  6.352330   0.1   

                                                  bam       depictio_run_id  \
0   /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
1   /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
2   /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
3   /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
4   /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
..                                                ...                   ...   
91  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-30...  2023-11-30-HWTM3AFX5   
92  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-30...  2023-11-30-HWTM3AFX5   
93  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-30...  2023-11-30-HWTM3AFX5   
94  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-30...  2023-11-30-HWTM3AFX5   
95  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-30...  2023-11-30-HWTM3AFX5   

    prediction  probability  year  
0            1       0.7984  2020  
1            1       0.9334  2020  
2            1       0.9318  2020  
3            0       0.1804  2020  
4            1       0.9227  2020  
..         ...          ...   ...  
91           1       0.8352  2023  
92           1       0.8622  2023  
93           1       0.7724  2023  
94           1       0.7902  2023  
95           1       0.5815  2023  

[19104 rows x 18 columns]

In [4]:
l_df = pd.read_parquet("strandscape_vizu_dev.parquet")
l_df

sample                    cell  medbin   mapped  suppl    dupl  \
0       HG03486x02       HG03486x02PE20501      14   812416    504  334936   
1       HG03486x02       HG03486x02PE20502      12   715809    477  275787   
2       HG03486x02       HG03486x02PE20503      20  1220951    703  521408   
3       HG03486x02       HG03486x02PE20504      20  1408977    790  671594   
4       HG03486x02       HG03486x02PE20505      12   789080    505  347438   
..             ...                     ...     ...      ...    ...     ...   
379  HGSVCpool3NEW  HGSVCpool3NEWiTRUE7G92       1   770771    462  689420   
380  HGSVCpool3NEW  HGSVCpool3NEWiTRUE7G93       0   252236    115  206995   
381  HGSVCpool3NEW  HGSVCpool3NEWiTRUE7G94       0   429080    240  372099   
382  HGSVCpool3NEW  HGSVCpool3NEWiTRUE7G95       0   299683    213  261260   
383  HGSVCpool3NEW  HGSVCpool3NEWiTRUE7G96      30  1575876   1008  478288   

      mapq   read2    good  pass1      nb_p      nb_r  nb_a  \
0    51265  212503  213208      1  0.028926  0.439206   0.1   
1    50360  194299  194886      1  0.028926  0.400842   0.1   
2    83466  307268  308106      1  0.028926  0.634170   0.1   
3    81942  326656  327995      1  0.028926  0.675949   0.1   
4    52432  194048  194657      1  0.028926  0.400715   0.1   
..     ...     ...     ...    ...       ...       ...   ...   
379  18336   29019   33534      0  0.000000  0.000000   0.0   
380   6707   18374   20045      0  0.000000  0.000000   0.0   
381  10904   21563   24274      0  0.000000  0.000000   0.0   
382   8162   14163   15885      0  0.000000  0.000000   0.0   
383  93425  495653  507502      1  0.162801  6.820590   0.1   

                                                   bam       depictio_run_id  \
0    /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
1    /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
2    /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
3    /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
4    /scratch/tweber/DATA/MC_DATA/STOCKS/2020-06-22...  2020-06-22-H5YMMAFX2   
..                                                 ...                   ...   
379  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-27...  2023-11-27-HNKL2AFX5   
380  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-27...  2023-11-27-HNKL2AFX5   
381  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-27...  2023-11-27-HNKL2AFX5   
382  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-27...  2023-11-27-HNKL2AFX5   
383  /scratch/tweber/DATA/MC_DATA/STOCKS/2023-11-27...  2023-11-27-HNKL2AFX5   

     prediction  probability  year  
0             1       0.7984  2020  
1             1       0.9334  2020  
2             1       0.9318  2020  
3             0       0.1804  2020  
4             1       0.9227  2020  
..          ...          ...   ...  
379           0       0.0000  2023  
380           0       0.0000  2023  
381           0       0.0000  2023  
382           0       0.0000  2023  
383           1       0.5746  2023  

[15840 rows x 18 columns]

In [5]:
px.violin(
    l_df, 
    x="sample",
    y="good",
    color="depictio_run_id",
    # facet_col="year",
    height=1000,
    hover_data=["depictio_run_id", "sample", "good"],
            points="all",
            box=True,
            

)



In [ ]:
px.box(
    l_df, 
    x="sample",
    y="good",
    color="depictio_run_id",
    # facet_col="year",
    height=1000,
    hover_data=["depictio_run_id", "sample", "good"],
            points="all",

)



In [77]:
import random
random.seed(1)


# Sample name to highlight
highlight_sample = l_df["sample"].iloc[random.randint(0, l_df.shape[0])]
print(highlight_sample)


fig = px.violin(
    l_df, 
    x="sample",
    y="good",
    color="depictio_run_id",
    # facet_col="year",
    height=1000,
    hover_data=["depictio_run_id", "sample", "cell", "good"],
            points="all",
            box=True

)





# Find the position of the highlighted sample in the x-axis
highlight_sample_position = l_df['sample'].unique().tolist().index(highlight_sample)
print(highlight_sample_position)

# Add a vertical line for the highlighted sample
fig.add_vline(x=highlight_sample_position, line_width=3, line_dash="dash", line_color="red")

# # Alternatively, add a rectangular shape to highlight the area
# fig.add_vrect(x0=highlight_sample_position-0.5, x1=highlight_sample_position+0.5, 
#               fillcolor="red", opacity=0.2, line_width=0)

ckAML02x03
22


In [2]:
import json
import plotly.express as px
import redis
from dash import dcc

# Create a Plotly figure
figure = px.scatter(x=[0, 1, 2, 3, 4], y=[0, 1, 4, 9, 16])

# Serialize the figure to JSON
figure_json = json.dumps(figure, cls=plotly.utils.PlotlyJSONEncoder)

# Connect to Redis
redis_client = redis.Redis(host='localhost', port=6379, db=0)

# Store the figure in Redis
# Assuming the key for storing the figure is 'my_figure'
redis_client.set('my_figure', figure_json)

# Later, when you need to retrieve the figure

# Check if the figure exists in Redis
if redis_client.exists('my_figure'):
    # Get the figure from Redis
    retrieved_figure_json = redis_client.get('my_figure')

    # Deserialize the JSON back to a Plotly figure
    retrieved_figure = json.loads(retrieved_figure_json, cls=plotly.utils.PlotlyJSONDecoder)

    # Use the figure in Dash
    dash_figure = dcc.Graph(figure=retrieved_figure)
else:
    # Handle the case where the figure does not exist in Redis
    # For example, use the original figure or display a message
    dash_figure = dcc.Graph(figure=figure)
    # Alternatively, you could display a message or take other appropriate actions

dash_figure

ModuleNotFoundError: No module named 'redis'